In [41]:
from mshr import *
from fenics import *
import numpy as np 

In [42]:
h = 0.05
w = 1.0
charge = 3 # coulombs
gap = 0.1
eps = 8.85e-12

domain_w = 2.0
domain_h = 2.0

order = 2

domain = Rectangle(Point(-domain_w,-domain_h),Point(domain_w,domain_h))

top_plate = Rectangle(Point(-0.5*w, 0.5*(gap)), Point(0.5*w, 0.5*(gap)+h))
bottom_plate = Rectangle(Point(-0.5*w, -0.5*(gap)), Point(0.5*w, -0.5*(gap)-h))

domain.set_subdomain(1, top_plate)
domain.set_subdomain(2, bottom_plate)

In [43]:
mesh = generate_mesh(domain, 64)

V = FunctionSpace(mesh, "CG", order)

def boundary(x, on_boundary):
    return on_boundary
bc = DirichletBC(V, Constant(0), boundary)

In [44]:
# creaste mesh function with unsigned integers corresponding to subdomain numbers
# with dimension 2, equal to the cell dimension
markers = MeshFunction('size_t', mesh, 2, mesh.domains())

plot(markers, title="Subdomains")

In [45]:
# redefine the integration measure
# we can use dx(0), dx(1),... to integrate over subdomains 0,1,...
dx = Measure('dx', domain = mesh, subdomain_data = markers)

In [47]:
class sigma(UserExpression): # UserExpression instead of Expression
    def __init__(self, markers, **kwargs):
        super().__init__(**kwargs) # This part is new!
        self.markers = markers

    def eval_cell(self, values, x, cell):
        if self.markers[cell.index] == 0:
            values[0] = 0.0 # vacuum
        elif self.markers[cell.index] == 1:
            values[0] = charge # plates
        else:
            values[0] = -1.0*charge # plates

charge_density = sigma(markers, degree=1)


In [49]:
A_z = TrialFunction(V)
v = TestFunction(V)

a = dot(grad(A_z), grad(v))*dx
L = sum(pow(eps, -1)*v*charge_density*dx(i) for i in [1,2])

A_z = Function(V)
solve(a==L, A_z, bc)

Calling FFC just-in-time (JIT) compiler, this may take some time.


In [50]:
plot(A_z)

In [51]:
W = VectorFunctionSpace(mesh, "CG", 2)
B = project(as_vector((A_z.dx(0), A_z.dx(1))), W)

Calling FFC just-in-time (JIT) compiler, this may take some time.


In [52]:
file_A_z = File("potential.pvd")
file_A_z << A_z
file_B = File("field.pvd")
file_B << B

In [53]:
plot(B)

In [62]:
xyz = V.tabulate_dof_coordinates()
x = xyz[:,0]
y = xyz[:,1]

Bx = np.array(B.sub(0).vector())
By = np.array(B.sub(1).vector())

In [ ]:
import matplotlib.pyplot as plt 
plt.quiver()